# Q1

In [135]:
using CSV

In [136]:
using DataFrames
using WGLMakie
using Statistics

In [137]:
alldata = CSV.read("data.csv", DataFrame)

20×6 DataFrame
 Row │ row    x      y      sigma_y  sigma_x  rho_xy  
     │ Int64  Int64  Int64  Int64    Int64    Float64 
─────┼────────────────────────────────────────────────
   1 │     1    201    592       61        9    -0.84
   2 │     2    244    401       25        4     0.31
   3 │     3     47    583       38       11     0.64
   4 │     4    287    402       15        7    -0.27
   5 │     5    203    495       21        5    -0.33
   6 │     6     58    173       15        9     0.67
   7 │     7    210    479       27        4    -0.02
   8 │     8    202    504       14        4    -0.05
   9 │     9    198    510       30       11    -0.84
  10 │    10    158    416       16        7    -0.69
  11 │    11    165    393       14        5     0.3
  12 │    12    201    442       25        5    -0.46
  13 │    13    157    317       52        5    -0.03
  14 │    14    131    311       16        6     0.5
  15 │    15    166    400       34        6     0.73
  16 │    16    160    337       31        5    -0.52
  17 │    17    186    423       42        9     0.9
  18 │    18    125    334       26        8     0.4
  19 │    19    218    533       16        6    -0.78
  20 │    20    146    344       22        5    -0.56

In [138]:
data = alldata[5:end, :];

In [139]:
xx = LinRange(50, 250, 25);

In [140]:
] add Optim

   Resolving package versions...
  No Changes to `~/.julia/environments/v1.8/Project.toml`
  No Changes to `~/.julia/environments/v1.8/Manifest.toml`


In [141]:
using Optim

In [142]:
function gaussian_log_likelihood(x, mean, sigma)
    return -sum(log.(sigma * sqrt(2*π)) .+ 0.5 * (x - mean).^2 ./ sigma.^2)
end

function objective_quad(params, x, y, sigma)
    q = params[1]
    m = params[2]
    b = params[3]
    
    y_pred = q .* x.^2 .+ m .*x .+ b
    return -gaussian_log_likelihood(y .+ 0., y_pred, sigma .+ 0.)
end

function objective_lin(params, x, y, sigma)
    m = params[1]
    b = params[2]
    
    y_pred = m .*x .+ b
    return -gaussian_log_likelihood(y .+ 0., y_pred, sigma .+ 0.)
end

objective_lin (generic function with 1 method)

In [143]:
q = Float64.(0);
m = Float64.(2);
b = Float64.(50);

In [144]:
result_quad = optimize(p -> objective_quad(p, data.x, data.y, data.sigma_y), [q, m, b]);
result_lin = optimize(p -> objective_lin(p, data.x, data.y, data.sigma_y), [m, b]);

In [145]:
q_quad, m_quad, b_quad = Optim.minimizer(result_quad)

3-element Vector{Float64}:
  0.0022989828677678252
  1.596022798906278
 72.89641889731419

In [146]:
m_lin, b_lin = Optim.minimizer(result_lin)

2-element Vector{Float64}:
  2.239922318298898
 34.0476433503552

In [147]:
xx = LinRange(50, 250, 25)

25-element LinRange{Float64, Int64}:
 50.0,58.3333,66.6667,75.0,83.3333,…,216.667,225.0,233.333,241.667,250.0

In [148]:
f = Figure()
Axis(f[1, 1])
errorbars!(data.x, data.y, data.sigma_y)
scatter!(data.x, data.y, markersize = 10, color = :black)
lines!(xx, q_quad .* xx .^2 .+ m_quad .* xx .+ b_quad)
lines!(xx, m_lin .* xx .+ b_lin)
f

In the above plot, you can see that the quadratic fit and the linear fit are not that different, in fact a approximately equal to 0.002, which is very close to zero. So essentially, the quadratic fit is like the linear one with minute differences.

# Jack Knife

- Quadratic Case

In [149]:
#=
    This jack_knife function is very similar to jack_knife dusting had, so I don't think it needs extra explanation.
=#
function jack_knife(data, starting_params, objective_func)
    n = length(data.x)
    m = size(starting_params)[1]
    jack_params = zeros(m, n)

    for i in 1:n
        xcopy = copy(data.x)
        deleteat!(xcopy, i)
        ycopy = copy(data.y)
        deleteat!(ycopy, i)
        scopy = copy(data.sigma_y)
        deleteat!(scopy, i)
        result = optimize(p -> objective_func(p, xcopy, ycopy, scopy), starting_params)
        @assert Optim.converged(result)
        jack_result = Optim.minimizer(result)
        for j in 1:m
            jack_params[j, i] = jack_result[j]
        end
    end
    return jack_params
end

jack_knife (generic function with 1 method)

In [150]:
jack_quad = jack_knife(data, [q, m, b], objective_quad);

In [151]:
function find_mstd(data, n)
    return mean(data), sqrt((n - 1) / n) * std(data)
end

find_mstd (generic function with 1 method)

In [152]:
n = length(data.x)
mean_Q_quad, sigma_Q_quad = find_mstd(jack_quad[1, :], n);
mean_M_quad, sigma_M_quad = find_mstd(jack_quad[2, :], n);
mean_B_quad, sigma_B_quad = find_mstd(jack_quad[3, :], n);

In [153]:
function calc_quad(xx, jack_params)
    q_quad, m_quad, b_quad = jack_params[1], jack_params[2], jack_params[3]
    return q_quad .* xx .^2 .+ m_quad .* xx .+ b_quad;
end

function calc_lin(xx, jack_params)
    m_lin, b_lin = jack_params[1], jack_params[2]
    return m_lin .* xx .+ b_lin;
end

#= 
plot_jack_knife parameters:
 - data: just the data that we had
 - optim_params_min: optimum values we find from the objective_functions (linear or quadratic)
 - jack_params: returning values of the jack_knife method
 - calc_func_main: the function (linear or quadratic) for which we found the jack_knife parameters.
 - calc_func_comp: the function (quadratic or linear) for which we did not run jack_knife this time around, it is just for comparison to the main function.
 - mean_params: mean values from the jack_knife parameters
 - std_params: std values from the jack_knife parameters
=# 
function plot_jack_knife(data, optim_params_main, optim_params_comp, jack_params, calc_func_main, calc_func_comp, 
        mean_params, std_params)
    f = Figure()
    Axis(f[1, 1])
    errorbars!(data.x, data.y, data.sigma_y)
    scatter!(data.x, data.y, markersize = 10, color = :black)
    # jack-knife line (of main optimized)
    for i in 1:n
        lines!(xx, calc_func_main(xx, jack_params[:, i]), color=:green)
    end
    # main optimized line
    lines!(xx, calc_func_main(xx, optim_params_main), color=:red, linewidth=3)
    # compare (for quad it is lin for lin it is quad) optimized line
    lines!(xx, calc_func_comp(xx, optim_params_comp), color=:blue, linewidth=3)
    lines!(xx, calc_func_main(xx, mean_params .+ std_params), color=:purple, linewidth=4)
    lines!(xx, calc_func_main(xx, mean_params .- std_params), color=:purple, linewidth=4)
    f
end

plot_jack_knife(data, [q_quad, m_quad, b_quad], [m_lin, b_lin], jack_quad, calc_quad, calc_lin,
                [mean_Q_quad, mean_M_quad, mean_B_quad], [sigma_Q_quad, sigma_M_quad, sigma_B_quad])

As you can see, in the quadratic case, the standard deviations of the lines found by the jack knife method is high enough to encompass all the points, at least within the error margin.

- Linear Case

In [154]:
jack_lin = jack_knife(data, [m, b], objective_lin);

In [155]:
mean_M_lin, sigma_M_lin = find_mstd(jack_lin[1, :], n);
mean_B_lin, sigma_B_lin = find_mstd(jack_lin[2, :], n);

In [156]:
plot_jack_knife(data, [m_lin, b_lin], [q_quad, m_quad, b_quad], jack_lin, calc_lin, calc_quad,
                [mean_M_lin, mean_B_lin], [sigma_M_lin, sigma_B_lin])

As you can see, adding the quadratic term allowed us to encompass more points within the margin. For the linear case some of the points are completely outside the margin (the purple lines), even their error bars lie outside the margin. It is conclusive then that the quadratic term makes the fitting result better.

# Stretch 1

* Chi-squared

We can calculate Chi-squared as follows:

In [157]:
function calc_chi_squared(data, params)
    y_pred = 0
    n = size(params)[1]
    for i in 1:n
        y_pred = y_pred .+ params[i] .* data.x .^ (n - i) 
    end
    return chi_squared = sum((data.y - y_pred).^2 ./ y_pred)
end

chi_lin = calc_chi_squared(data, [m_lin, b_lin])

35.67023771148439

In [158]:
chi_quad = calc_chi_squared(data, [q_quad, m_quad, b_quad])

32.75459117501412

In [159]:
chi_quad - chi_lin

-2.9156465364702697

Chi-squared error is smaller for the quadratic fit (by more than 1 so it is significant). So we can say that quadratic fit is conculsively a better fit than the linear one.

* AIC

In [160]:
function calc_AIC(data, params, objective_func)
    return 2 .* size(params)[1] .+ 2 .* objective_func(params, data.x, data.y, data.sigma_y)
end
calc_AIC(data, [m_lin, b_lin], objective_lin)

152.61233016426175

In [161]:
calc_AIC(data, [q_quad, m_quad, b_quad], objective_quad)

153.33473216904653

* BIC

In [162]:
function calc_BIC(data, params, objective_func)
    k = size(params)[1]
    n = size(data.x)[1]
    return k .* log(n) .+ 2 .* objective_func(params, data.x, data.y, data.sigma_y)
end

calc_BIC(data, [m_lin, b_lin], objective_lin)

154.1575076087413

In [163]:
calc_BIC(data, [q_quad, m_quad, b_quad], objective_quad)

155.65249833576587

AIC and BIC give the opposite result. In AIC and BIC, as the complexity of the model increases, BIC and AIC increase and as the likelihood increases, BIC and AIC decrease. So a bigger likelihood doesn't always result in a better fit based on its AIC and BIC values. So, based on BIC and AIC of the models, eventhough the quadratic model increases the likelihood, it doesn't increase it a significant amount, it doens't compensate for the extra complexity of the quadratic fit.

# Q2

* m, b plane for 1 point

In [164]:
function plot_contours_lin(data, optim_params, num, objective_func, b_range, m_range, levels)
    # Range of m,b values to plot
    bvals = LinRange(b_range[1], b_range[2], Int64.(b_range[3]))
    mvals = LinRange(m_range[1], m_range[2], Int64.(m_range[3]))
    # Compute the objective function for each point in a grid
    og = [objective_func([m, b], data.x[1:num], data.y[1:num], data.sigma_y[1:num])
          for b in bvals, m in mvals]
    f = Figure()
    Axis(f[1, 1])
    contour!(bvals, mvals, og, levels=levels)
    scatter!(optim_params[2], optim_params[1], markersize = 10, color = :black)
    f
end

plot_contours_lin(data, [m_lin, b_lin], 1, objective_lin, [0., 60., 100], [2.0, 2.5, 100], 1000)

If optimization were done on one single point, the optimal values for m and b would like in the white region of the above plot. Note that we wouldn't have found unique values because infintely many lines can pass through one point.

* m, b plane for 2 points

In [165]:
plot_contours_lin(data, [m_lin, b_lin], 2, objective_lin, [0., 60., 100], [2.0, 2.5, 100], 1000)

Now you can see we have a region of maximum constrained inside an ellipse, this is because we have two points to fit a line to. For two points we will have a unique optimum value.

* m, b plane for all 16 points

In [166]:
plot_contours_lin(data, [m_lin, b_lin], 16, objective_lin, [0., 60., 100], [2.0, 2.5, 100], 1000)

Now that we have used all the points, we see that the optimum value found with the method we used in q1 matches perfectly with the the maximum shown with the contours, which is a good sanity check for our previous optimization method and its validity.

#### Contour plot for outlier-rejecting version

In [167]:
result = optimize(p -> objective_lin(p, alldata.x, alldata.y, alldata.sigma_y),
                  [m, b])
@assert Optim.converged(result)
m_bad, b_bad = Optim.minimizer(result)

2-element Vector{Float64}:
   1.076748906719455
 213.2736217150296

In [168]:
f = Figure()
Axis(f[1, 1])
errorbars!(alldata.x, alldata.y, alldata.sigma_y)
scatter!(alldata.x, alldata.y, markersize=20, color=:red)

yy_bad = xx .* m_bad .+ b_bad
lines!(xx, yy_bad, color=:purple, linewidth=3)

f

In [169]:
function objective_outliers(parameters, x, y, sigma)
    b = parameters[2]
    m = parameters[1]
    
    frac_bad = 0.01
    like_bad = frac_bad * (1. / 600.)

    y_pred = b .+ m .* x
    like_good = (1. - frac_bad) * 1 ./(sqrt(2*π) .* sigma) .* exp.(-0.5 * (y .- y_pred).^2 ./ sigma.^2)
    like = like_bad .+ like_good
    loglike = log.(like)

    return -sum(loglike)
end

objective_outliers (generic function with 1 method)

In [170]:
starting_params = [m, b]
result_rej = optimize(p -> objective_outliers(p, alldata.x, alldata.y, alldata.sigma_y),
                  starting_params)
@assert Optim.converged(result_rej)
m_out, b_out = Optim.minimizer(result_rej)

2-element Vector{Float64}:
  2.252659398988028
 32.71335736732801

In [171]:
starting_params = [-0.5, 700 + 0.]
result = optimize(p -> objective_outliers(p, alldata.x, alldata.y, alldata.sigma_y),
                  starting_params)
@assert Optim.converged(result)
m_punk, b_punk = Optim.minimizer(result)

2-element Vector{Float64}:
  -0.7590088958472745
 627.9728284643311

In [172]:
f = Figure()
Axis(f[1, 1])
errorbars!(alldata.x, alldata.y, alldata.sigma_y)
scatter!(alldata.x, alldata.y, markersize=20, color=:red)

yy_bad = xx .* m_bad .+ b_bad
lines!(xx, yy_bad, color=:purple, linewidth=3)

yy_out = xx .* m_out .+ b_out
lines!(xx, yy_out, color=:green, linewidth=3)

yy_punk = xx .* m_punk .+ b_punk
lines!(xx, yy_punk, color=:blue, linewidth=3)

f

In [173]:
jack_out = jack_knife(alldata, [m, b], objective_outliers);

In [174]:
n_all = size(data.x)[1]
mean_M_out, sigma_M_out = find_mstd(jack_out[1, :], n_all);
mean_B_out, sigma_B_out = find_mstd(jack_out[2, :], n_all);

In [175]:
plot_jack_knife(alldata, [m_out, b_out], [m_bad, b_bad], jack_out, calc_lin, calc_lin, 
        [mean_M_out, mean_B_out], [sigma_M_out, sigma_B_out])

In [176]:
plot_contours_lin(alldata, [m_out, b_out], size(alldata)[1], objective_outliers, [0., 750., 100], [-1., 2.7, 100], 150)

# Q3.

In [177]:
x_prime = data.x .- mean(data.x);

In [178]:
result_prime = optimize(p -> objective_lin(p, x_prime, data.y, data.sigma_y), [m, b]);
m_prime, b_prime = Optim.minimizer(result_prime)

2-element Vector{Float64}:
   2.2399172609458327
 409.79367128785134

In [179]:
jack_prime = jack_knife(data, [m, b], objective_lin);

In [180]:
mean_M_prime, sigma_M_prime = find_mstd(jack_prime[1, :], n);
mean_B_prime, sigma_B_prime = find_mstd(jack_prime[2, :], n);
plot_jack_knife(data, [m_prime, b_prime], [m_lin, b_lin], jack_prime, calc_lin, calc_lin,
                [mean_M_prime, mean_B_prime], [sigma_M_prime, sigma_B_prime])

In [181]:
data_prime = DataFrame(x = x_prime, 
               y = data.y,
               sigma_y = data.sigma_y
               )
plot_contours_lin(data_prime, [m_prime, b_prime], size(data)[1], objective_lin, [0., 750., 100], [-2., 4, 100], 150)

It is evident from the above plot that the covariance matrix is simpler. It is almost diagonal, which means m' & b' are uncorrelated, or almost uncorrelated.

The transformation we did was:
y = m' x' + b' 
or:
y = m' (x - x_mean) + b'
So the original values of m & b are:
m = m'
b = b' - m' * x_mean

In [182]:
using Printf
m_original = m_prime;
b_original = b_prime - m_prime * mean(data.x);
@printf("m_original: %f\n", m_original)
@printf("b_original: %f", b_original)

m_original: 2.239917
b_original: 34.047551

Which agree almost perfectly with the m_lin & b_lin that we found in previous questions:

In [183]:
@printf("m_lin: %f\n", m_lin)
@printf("b_lin: %f", b_lin)

m_lin: 2.239922
b_lin: 34.047643

# Stretch 4

If you look at the jack_knife function or other related functions in this notebook, they are factored out and the factored out functions are used multiple times.